In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
!pip install transformers datasets peft accelerate bitsandbytes trl safetensors torch --no-cache

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 6.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.1/199.1 kB 15.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 297.3/297.3 kB 16.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.2/102.2 MB 84.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 225.0/225.0 kB 211.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 189.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 209.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 188.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 80.1/80.1 kB 177.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 96.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 243.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 54.2 MB/s eta 0:00:00
     

In [26]:
import torch
import pandas as pd
from functools import partial
from datasets import Dataset
from transformers import TrainingArguments
import time
import transformers
from sklearn.model_selection import train_test_split
from peft import LoraConfig, prepare_model_for_kbit_training, get_peft_model
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

column_names = ['H','RH','sentiment']
# base_path = '/content/drive/My Drive/Colab Notebooks/CSCI 564 NLP'
# df = pd.read_csv(f'{base_path}/hindi_data/romanized_hindi_english_paper.csv', names=column_names,nrows=8000)

path = '/content/drive/MyDrive/Project_544/data/hindi_data/romanized_hindi_sentiment_paper.csv'

df = pd.read_csv(path)
df.columns = column_names

In [27]:
df.head(3)

H  \
0  लोग वतन तक खा जाते हैं इसका इसे यकीन नहींमान ज...   
1  गुमनाम है वतन पर मिटने वाले लोग आतन्कवादियों स...   
2  ज़ंजीर बदली जा रही थी मैं समझा था रिहाई हो गयी है   

                                                  RH sentiment  
0  log watan taka khaa jaate hain iska ise yakeen...  negative  
1  gumnam hai watan para mitane vaale log aatankv...  negative  
2  zanjeer badli jaa rahee thee main samajha tha ...  negative

In [8]:
# Hugging Face model name
#model_name = "microsoft/phi-2" # not the larger version - need to look into this
model_name = "TinyLlama/TinyLlama-1.1B-Chat-v1.0"
use_flash_attention = False


# BitsAndBytesConfig int-4 config
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
)

# Load model
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    # quantization_config=bnb_config,
    use_cache=False,
    use_flash_attention_2=use_flash_attention,
    device_map="auto",
    torch_dtype=torch.float16
)

model.config.pretraining_tp = 1

# Load tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/608 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/2.20G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.29k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/551 [00:00<?, ?B/s]

In [9]:
# LoRA config based on QLoRA paper
peft_config = LoraConfig(
    lora_alpha=32,
    lora_dropout=0.1,
    r=16,
    bias="none",
    task_type="CAUSAL_LM",
)
# Prepare model for training
model = prepare_model_for_kbit_training(model)
model = get_peft_model(model, peft_config)

In [28]:
# for sentiment analysis
train_df, val_df = train_test_split(df, test_size=0.2, random_state=42)
val_df, test_df = train_test_split(val_df, test_size=0.5, random_state=42)

In [ ]:
# results = {'Languages': [],
#            'Avg Sentence BLEU' : [],
#            'Corpus BLEU' : []}

# **Hindi Sentiment Analysis**

In [11]:
train_df, val_df = train_df, val_df
val_df, test_df = val_df, test_df

In [29]:
train_df2, val_df2 = train_df.copy(), val_df.copy()
val_df2, test_df2 = val_df.copy(), test_df.copy()

In [30]:
train_df3, val_df3 = train_df.copy(), val_df.copy()
val_df3, test_df3 = val_df.copy(), test_df.copy()

In [14]:
def preprocess_batch(batch, tokenizer, max_length):
    """
    Tokenizing a batch
    """
    print(batch)
    return tokenizer(
        batch["text"],
        max_length=max_length,
        truncation=True,
    )


_preprocessing_function = partial(preprocess_batch, max_length=1024, tokenizer=tokenizer)

def create_prompt(row):
    return f"Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\nHindi: {row['H']} \nOutput: {row['sentiment']}"

# Apply the function to each row and create a new 'text' column
train_df['text'] = train_df.apply(create_prompt, axis=1)
val_df['text'] = val_df.apply(create_prompt, axis=1)

columns_to_drop = ['H','RH','sentiment']
train_df.drop(columns=columns_to_drop, inplace=True)
val_df.drop(columns=columns_to_drop, inplace=True)

train_dataset = Dataset.from_pandas(train_df)
val_dataset= Dataset.from_pandas(val_df)


In [15]:
train_dataset = train_dataset.map(
        _preprocessing_function,
        batched=True,
    )

Map:   0%|          | 0/7261 [00:00<?, ? examples/s]

{'text': ["Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\nHindi: RT @aajtak: दिल्ली-एनसीआर में ठंड का एहसास ज्यादा हो रहा है पिछले 2 दिनों से तेज गति से हवाएं चल रही हैं जिसकी वजह से टेंपरेचर डाउन हो गया… \nOutput: neutral", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\nHindi: उन्होंने फिजूलखर्ची पर बच्चों को सन्देश देने की खातिर एक अरब छब्बीस करोड़ फिजूल में खर्च कर दिए यही नहीं बिजली \nOutput: negative", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\nHindi: दिल्ली के दर्शकों को पीटरसन से धमाकेदार पारी की उम्मीद रहेगी, \nOutput: positive", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive'

In [16]:
val_dataset = val_dataset.map(
        _preprocessing_function,
    batched=True,
    )

Map:   0%|          | 0/908 [00:00<?, ? examples/s]

{'text': ["Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\nHindi: आतंकी हाफिज के गेम प्लान का खुलासा, कश्मीर में ISI का टैलेंट हंट कैंप https://t.co/yQZWPZP3uE \r\n@aajtak \nOutput: neutral", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\nHindi: RT @itsparvezsagar: डेटिंग ऐप पर युवती की धमकी- 'दिल्ली में होगा न्यूक्लियर धमाका, उड़ेगा राष्ट्रपति भवन'\r\nhttps://t.co/SZ0lJkyvbX\r\n-\r\n@Aajtak… \nOutput: neutral", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\nHindi: उन्हें हिन्दी ठीक से बोलने नहीं आती फिर भी उन्होंने बॉलीवुड में कदम रखा और हिंदी बोलना सीखा। \nOutput: positive", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The

In [17]:
base_path = "/content/drive/My Drive/CSCI544ProjOutput/"
output_dir = f'{base_path}/peft-dialogue-summary-training-{str(int(time.time()))}'
peft_training_args = TrainingArguments(
    output_dir = output_dir,
    warmup_steps=1,
    per_device_train_batch_size=1,
    gradient_accumulation_steps=4,
    max_steps=50,
    learning_rate=2e-4,
    optim="paged_adamw_8bit",
    logging_steps=25,
    logging_dir="./logs",
    save_strategy="steps",
    save_steps=25,
    evaluation_strategy="steps",
    eval_steps=25,
    do_eval=True,
    gradient_checkpointing=False,
    report_to="none",
    overwrite_output_dir = 'True',
    group_by_length=True,
)

model.config.use_cache = False

peft_trainer = transformers.Trainer(
    model=model,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    args=peft_training_args,
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [18]:
print(type(train_dataset['text'][0]))

<class 'str'>


In [19]:
peft_trainer.train()

TrainOutput(global_step=50, training_loss=1.292042236328125, metrics={'train_runtime': 286.4916, 'train_samples_per_second': 0.698, 'train_steps_per_second': 0.175, 'total_flos': 175227830808576.0, 'train_loss': 1.292042236328125, 'epoch': 0.03})

In [20]:
from nltk.translate.bleu_score import corpus_bleu, sentence_bleu

# Assume test_data is a list of tuples: (source_sentence, reference_translation)

sources = test_df['H'].to_list()
references = test_df['sentiment'].to_list()

#sources = [sources[0]]
#references = [references[0]]

s = []
r = []

for i in range(len(sources)):

    inputs = tokenizer(f'''Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative' \nHindi: {sources[i]} \nOutput:''', return_tensors="pt",)

    with torch.no_grad():
        outputs = model.generate(input_ids=inputs["input_ids"].to("cuda"), max_new_tokens=20)
        text = tokenizer.batch_decode(outputs)[0]
        #print(text)

    #print(text)
    t = text.split("\nOutput: ")
    t = t[1]. split("\n")[0]

    """
    print("t")
    print(t)
    print(t.split())
    print(references[i].split())
    print("---")
    """

    s.append(t)
    r.append(references[i])

In [21]:
print(s)
print(r)

['positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'negative', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'negative', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'positive', 'negative', 'positive', 'positive', 'positive', 'positive', 'positive', 'po

In [22]:
valid_labels = {'positive', 'negative', 'neutral'}
filtered_ground_truth = []
filtered_predicted = []
for gt, pred in zip(s, r):
    if gt in valid_labels and pred in valid_labels:
        filtered_ground_truth.append(gt)
        filtered_predicted.append(pred)

# Calculate accuracy
correct_predictions = sum(1 for gt, pred in zip(filtered_ground_truth, filtered_predicted) if gt == pred)
total_predictions = len(filtered_ground_truth)
h_accuracy = correct_predictions / total_predictions if total_predictions > 0 else 0.0
h_accuracy

0.3700440528634361

In [ ]:
# peft_trainer.save_model('/content/drive/My Drive/CSCI544ProjOutput/saved_model')
# tokenizer.save_pretrained('/content/drive/My Drive/CSCI544ProjOutput/saved_tokenizer')

#**Romanized Hindi to English**

In [31]:
train_df, val_df = train_df2, val_df2
val_df, test_df = val_df2, test_df2
train_df

H  \
2549  RT @aajtak: दिल्ली-एनसीआर में ठंड का एहसास ज्य...   
218   उन्होंने फिजूलखर्ची पर बच्चों को सन्देश देने क...   
3768  दिल्ली के दर्शकों को पीटरसन से धमाकेदार पारी क...   
8947  RT @aajtak: हम उत्तर प्रदेश की जनता की अपेक्षा...   
3238  जलवा खतम हो रहा है ये सिर्फ मरे हुवों की मदद क...   
...                                                 ...   
5734                     राम अजाति लोगों की मदद करता है   
5191                   इससे आपके कंधे ताकतवर बन सकेंगे।   
5390  सभी काजी की इस अनोखी तरकीब की प्रशंसा कर रहे थे।    
860   @jitendrsg @SachinArorra @FarOutAkhtar @vidya_...   
7270  अच्छे दिन आने वाले हैं ये उम्मीद तो अच्छी है, ...   

                                                     RH sentiment  
2549  rt @aajtak: dilli-ncr main thanda kaa ehsas zy...   neutral  
218   unhone fizulkharchi para bachchon quo sandesh ...  negative  
3768  dilli key darshakon quo pieterson say dhamaked...  positive  
8947  rt @aajtak: humm utter pradesh key janata key ...   neutral  
3238  jalwa khatam how rahaa hai yeye sirf marey huv...  negative  
...                                                 ...       ...  
5734              rama ajaati logon key madad karta hai  positive  
5191         isase aapke kandhe taakatvar bunn sakenge.  positive  
5390  sabhi kaaji key iss anokhi tarkib key prashans...  positive  
860   @jitendrsg @sachinarorra @faroutakhtar @vidya_...  positive  
7270  achche dinn aane vaale hain yeye ummid too ach...  negative  

[7261 rows x 3 columns]

In [32]:
def preprocess_batch(batch, tokenizer, max_length):
    """
    Tokenizing a batch
    """
    print(batch)
    return tokenizer(
        batch["text"],
        max_length=max_length,
        truncation=True,
    )


_preprocessing_function = partial(preprocess_batch, max_length=1024, tokenizer=tokenizer)

def create_prompt(row):
    return f"Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\Hindi Transliterated: {row['RH']} \nOutput: {row['sentiment']}"

# Apply the function to each row and create a new 'text' column
train_df['text'] = train_df.apply(create_prompt, axis=1)
val_df['text'] = val_df.apply(create_prompt, axis=1)

columns_to_drop = ['H','RH','sentiment']
train_df.drop(columns=columns_to_drop, inplace=True)
val_df.drop(columns=columns_to_drop, inplace=True)

train_dataset = Dataset.from_pandas(train_df)
val_dataset= Dataset.from_pandas(val_df)


In [33]:
train_dataset = train_dataset.map(
        _preprocessing_function,
        batched=True,
    )

Map:   0%|          | 0/7261 [00:00<?, ? examples/s]

{'text': ["Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\\Hindi Transliterated: rt @aajtak: dilli-ncr main thanda kaa ehsas zyada how rahaa hai pichhale 2 dino say tez gati say havaaen chal rahee hain jisaki vajah say temperature down how gaya… \nOutput: neutral", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\\Hindi Transliterated: unhone fizulkharchi para bachchon quo sandesh dene key khaatir ack arab chhabbis karod fizul main kharch curr die yahee nahin bijli \nOutput: negative", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\\Hindi Transliterated: dilli key darshakon quo pieterson say dhamakedar paari key ummid rahegi, \nOutput: positive", "Classify the sentiment 

In [34]:
val_dataset = val_dataset.map(
        _preprocessing_function,
    batched=True,
    )

Map:   0%|          | 0/908 [00:00<?, ? examples/s]

{'text': ["Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\\Hindi Transliterated: aatanki hafiz key game plan kaa khulasa, kashmir main isi kaa talent hunt camp https://t.co/yqzwpzp3ue \r\n@aajtak \nOutput: neutral", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\\Hindi Transliterated: rt @itsparvezsagar: dating aip para yuvati key dhamki- 'dilli main hoga nuclear dhamaka, udegaa rashtrapati bhawan'\r\nhttps://t.co/sz0ljkyvbx\r\n-\r\n@aajtak… \nOutput: neutral", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'.\\Hindi Transliterated: unhein hindi theek say bolane nahin aatee fir bhi unhone bollywood main kadam rakhaa our hindi bolna seekha. \nOutput: positive", "Classify t

In [35]:
base_path = "/content/drive/My Drive/CSCI544ProjOutput/"
output_dir = f'{base_path}/peft-dialogue-summary-training-{str(int(time.time()))}'
peft_training_args = TrainingArguments(
    output_dir = output_dir,
    warmup_steps=1,
    per_device_train_batch_size=1,
    gradient_accumulation_steps=4,
    max_steps=50,
    learning_rate=2e-4,
    optim="paged_adamw_8bit",
    logging_steps=25,
    logging_dir="./logs",
    save_strategy="steps",
    save_steps=25,
    evaluation_strategy="steps",
    eval_steps=25,
    do_eval=True,
    gradient_checkpointing=False,
    report_to="none",
    overwrite_output_dir = 'True',
    group_by_length=True,
)

model.config.use_cache = False

peft_trainer = transformers.Trainer(
    model=model,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    args=peft_training_args,
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [36]:
print(type(train_dataset['text'][0]))

<class 'str'>


In [37]:
peft_trainer.train()

TrainOutput(global_step=50, training_loss=2.0773501586914063, metrics={'train_runtime': 188.2262, 'train_samples_per_second': 1.063, 'train_steps_per_second': 0.266, 'total_flos': 123173924450304.0, 'train_loss': 2.0773501586914063, 'epoch': 0.03})

In [38]:
from nltk.translate.bleu_score import corpus_bleu, sentence_bleu

# Assume test_data is a list of tuples: (source_sentence, reference_translation)

sources = test_df['RH'].to_list()
references = test_df['sentiment'].to_list()

#sources = [sources[0]]
#references = [references[0]]

s = []
r = []

for i in range(len(sources)):

    inputs = tokenizer(f'''Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative' \nHindi Transliterated: {sources[i]} \nOutput:''', return_tensors="pt",)

    with torch.no_grad():
        outputs = model.generate(input_ids=inputs["input_ids"].to("cuda"), max_new_tokens=20)
        text = tokenizer.batch_decode(outputs)[0]
        #print(text)

    #print(text)
    t = text.split("\nOutput: ")
    t = t[1]. split("\n")[0]

    """
    print("t")
    print(t)
    print(t.split())
    print(references[i].split())
    print("---")
    """

    s.append(t)
    r.append(references[i])

In [39]:
print(s)
print(r)

['negative', 'positive', 'positive', 'positive', 'negative', 'positive', 'negative', 'negative', 'positive', 'positive', 'positive', 'positive', 'positive', 'negative', 'positive', 'positive', 'positive', 'negative', 'positive', 'negative', 'neutral ', 'negative', 'negative', 'positive', 'positive', 'negative', 'negative', 'positive', 'positive', 'positive', 'negative', 'neutral', 'negative', 'positive', 'negative', 'negative', 'negative', 'negative', 'negative', 'positive', 'negative', 'negative', 'positive', 'positive', 'neutral', 'neutral', 'neutral', 'negative', 'positive', 'negative', 'negative', 'negative', 'negative', 'negative', 'positive', 'negative', 'negative', 'positive', 'negative', 'positive', 'negative', 'negative', 'positive', 'positive', 'positive', 'positive', 'negative', 'negative', 'positive', 'negative', 'neutral', 'negative', 'positive', 'positive', 'negative', 'negative', 'positive', 'negative', 'positive', 'negative', 'negative', 'positive', 'positive', 'positiv

In [40]:
valid_labels = {'positive', 'negative', 'neutral'}
filtered_ground_truth = []
filtered_predicted = []
for gt, pred in zip(s, r):
    if gt in valid_labels and pred in valid_labels:
        filtered_ground_truth.append(gt)
        filtered_predicted.append(pred)

# Calculate accuracy
correct_predictions = sum(1 for gt, pred in zip(filtered_ground_truth, filtered_predicted) if gt == pred)
total_predictions = len(filtered_ground_truth)
rh_accuracy = correct_predictions / total_predictions if total_predictions > 0 else 0.0
rh_accuracy

0.4564732142857143

# **RH + H to English**

In [62]:
train_df, val_df = train_df3, val_df3
val_df, test_df = val_df3, test_df3

In [63]:

def preprocess_batch(batch, tokenizer, max_length):
    """
    Tokenizing a batch
    """
    print(batch)
    return tokenizer(
        batch["text"],
        max_length=max_length,
        truncation=True,
    )


_preprocessing_function = partial(preprocess_batch, max_length=1024, tokenizer=tokenizer)
# Convert train_df and val_df into JSON format
# train_dataset = [create_json_record(row, "train") for _, row in train_df.iterrows()]
# val_dataset = [create_json_record(row, "val") for _, row in val_df.iterrows()]


def create_prompt(row):
    return f"Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative' \nHindi: {row['H']} \nHindi Transliterated:  {row['RH']} \nOutput: {row['sentiment']}"

# Apply the function to each row and create a new 'text' column
train_df['text'] = train_df.apply(create_prompt, axis=1)
val_df['text'] = val_df.apply(create_prompt, axis=1)

columns_to_drop = ['H', 'RH','sentiment']
train_df.drop(columns=columns_to_drop, inplace=True)
val_df.drop(columns=columns_to_drop, inplace=True)

train_dataset = Dataset.from_pandas(train_df)
val_dataset= Dataset.from_pandas(val_df)


KeyError: 'H'

In [45]:
train_dataset = train_dataset.map(
        _preprocessing_function,
        batched=True,
    )

Map:   0%|          | 0/7261 [00:00<?, ? examples/s]

{'text': ["Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative' \nHindi: RT @aajtak: दिल्ली-एनसीआर में ठंड का एहसास ज्यादा हो रहा है पिछले 2 दिनों से तेज गति से हवाएं चल रही हैं जिसकी वजह से टेंपरेचर डाउन हो गया… \nHindi Transliterated:  rt @aajtak: dilli-ncr main thanda kaa ehsas zyada how rahaa hai pichhale 2 dino say tez gati say havaaen chal rahee hain jisaki vajah say temperature down how gaya… \nOutput: neutral", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative' \nHindi: उन्होंने फिजूलखर्ची पर बच्चों को सन्देश देने की खातिर एक अरब छब्बीस करोड़ फिजूल में खर्च कर दिए यही नहीं बिजली \nHindi Transliterated:  unhone fizulkharchi para bachchon quo sandesh dene key khaatir ack arab chhabbis karod fizul main kharch curr die yahee nahin bijli \nOutput: negative", "Classify the sentiment o

In [46]:
val_dataset = val_dataset.map(
        _preprocessing_function,
    batched=True,
    )

Map:   0%|          | 0/908 [00:00<?, ? examples/s]

{'text': ["Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative' \nHindi: आतंकी हाफिज के गेम प्लान का खुलासा, कश्मीर में ISI का टैलेंट हंट कैंप https://t.co/yQZWPZP3uE \r\n@aajtak \nHindi Transliterated:  aatanki hafiz key game plan kaa khulasa, kashmir main isi kaa talent hunt camp https://t.co/yqzwpzp3ue \r\n@aajtak \nOutput: neutral", "Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative' \nHindi: RT @itsparvezsagar: डेटिंग ऐप पर युवती की धमकी- 'दिल्ली में होगा न्यूक्लियर धमाका, उड़ेगा राष्ट्रपति भवन'\r\nhttps://t.co/SZ0lJkyvbX\r\n-\r\n@Aajtak… \nHindi Transliterated:  rt @itsparvezsagar: dating aip para yuvati key dhamki- 'dilli main hoga nuclear dhamaka, udegaa rashtrapati bhawan'\r\nhttps://t.co/sz0ljkyvbx\r\n-\r\n@aajtak… \nOutput: neutral", "Classify the sentiment of the below Hindi 

In [47]:
base_path = "/content/drive/My Drive/CSCI544ProjOutput/"
output_dir = f'{base_path}/peft-dialogue-summary-training-{str(int(time.time()))}'
peft_training_args = TrainingArguments(
    output_dir = output_dir,
    warmup_steps=1,
    per_device_train_batch_size=1,
    gradient_accumulation_steps=4,
    max_steps=50,
    learning_rate=2e-4,
    optim="paged_adamw_8bit",
    logging_steps=25,
    logging_dir="./logs",
    save_strategy="steps",
    save_steps=25,
    evaluation_strategy="steps",
    eval_steps=25,
    do_eval=True,
    gradient_checkpointing=False,
    report_to="none",
    overwrite_output_dir = 'True',
    group_by_length=True,
)

model.config.use_cache = False

peft_trainer = transformers.Trainer(
    model=model,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    args=peft_training_args,
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [48]:
print(type(train_dataset['text'][0]))

<class 'str'>


In [49]:
peft_trainer.train()

TrainOutput(global_step=50, training_loss=1.1334032821655273, metrics={'train_runtime': 373.5929, 'train_samples_per_second': 0.535, 'train_steps_per_second': 0.134, 'total_flos': 242416435322880.0, 'train_loss': 1.1334032821655273, 'epoch': 0.03})

In [ ]:
# model = AutoModelForCausalLM.from_pretrained('/content/drive/My Drive/peft-dialogue-summary-training-1712294967/checkpoint-375')
# tokenizer = AutoTokenizer.from_pretrained('/content/drive/My Drive/CSCI544ProjOutput/peft-dialogue-summary-training-1712294967/checkpoint-375',trust_remote_code=True)

In [54]:
from nltk.translate.bleu_score import corpus_bleu, sentence_bleu

# Assume test_data is a list of tuples: (source_sentence, reference_translation)

rh = test_df['RH'].to_list()
h = test_df['H'].to_list()
references = test_df['sentiment'].to_list()

#sources = [sources[0]]
#references = [references[0]]

s = []
r = []

for i in range(len(rh)):

    inputs = tokenizer(f"Classify the sentiment of the below Hindi sentence into Positive, Neutral or Negative. The output should be either 'Positive' or 'Neutral' or 'Negative'. \nHindi: {h[i]} \nHindi Transliterated: {rh[i]} \nOutput: ", return_tensors="pt",)

    with torch.no_grad():
        outputs = model.generate(input_ids=inputs["input_ids"].to("cuda"), max_new_tokens=20)
        text = tokenizer.batch_decode(outputs)[0]
        #print(text)

    #print(text)
    t = text.split("\nOutput: ")
    t = t[1]. split("\n")[0]

    """
    print("t")
    print(t)
    print(t.split())
    print(references[i].split())
    print("---")
    """

    s.append(t)
    # translations.append(reference.split())
    r.append(references[i])  # Note: reference must be a list of lists for corpus_bleu

In [55]:
print(s)

[' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' negative ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' positive ', ' negative ', ' positive ', ' positive ', ' positive ', ' positive ', ' positi

In [56]:
print(r)

['negative', 'neutral', 'positive', 'positive', 'negative', 'neutral', 'negative', 'negative', 'negative', 'neutral', 'neutral', 'positive', 'positive', 'positive', 'neutral', 'neutral', 'neutral', 'positive', 'neutral', 'negative', 'neutral', 'positive', 'negative', 'neutral', 'negative', 'negative', 'negative', 'positive', 'negative', 'neutral', 'negative', 'neutral', 'negative', 'neutral', 'positive', 'negative', 'neutral', 'negative', 'positive', 'neutral', 'negative', 'positive', 'neutral', 'positive', 'neutral', 'neutral', 'neutral', 'negative', 'neutral', 'positive', 'positive', 'positive', 'negative', 'positive', 'neutral', 'positive', 'negative', 'negative', 'positive', 'neutral', 'negative', 'positive', 'positive', 'positive', 'negative', 'neutral', 'negative', 'positive', 'negative', 'negative', 'neutral', 'positive', 'neutral', 'neutral', 'negative', 'positive', 'positive', 'negative', 'positive', 'positive', 'positive', 'neutral', 'neutral', 'positive', 'positive', 'positi

In [61]:
valid_labels = {'positive', 'negative', 'neutral'}
filtered_ground_truth = []
filtered_predicted = []
for gt, pred in zip(s, r):
    gt = gt.strip()
    if gt in valid_labels and pred in valid_labels:
        filtered_ground_truth.append(gt)
        filtered_predicted.append(pred)

# Calculate accuracy
correct_predictions = sum(1 for gt, pred in zip(filtered_ground_truth, filtered_predicted) if gt == pred)
total_predictions = len(filtered_ground_truth)
h_rh_accuracy = correct_predictions / total_predictions if total_predictions > 0 else 0.0
h_rh_accuracy

0.368942731277533

# **Results**

In [ ]:
# results_df = pd.DataFrame(results)
# results_df

Languages  Avg Sentence BLEU  Corpus BLEU
0                    Hindi -> English           0.284860     0.369188
1          Romanized Hindi -> English           0.287289     0.391789
2  Hindi + Romanized Hindi -> English           0.375024     0.404876